In [1]:
from transformers import CamembertTokenizer, CamembertModel, AutoTokenizer, AutoModel,AutoModelForSequenceClassification, utils, BertModel, BertTokenizer
import torch
from scipy.spatial.distance import cosine
from bertviz import model_view, head_view
import itertools
from IPython import display
import matplotlib.pyplot as plt
import numpy as np

c:\Users\Etudiant\M1_TAL\m1-supervised-project\.venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [14]:
# Initialisation du tokenizer et du modèle CamemBERT large
model_version= "dangvantuan/sentence-camembert-large"


def similarityCalcul(model_version):
    tokenizer = AutoTokenizer.from_pretrained(model_version)
    model = AutoModel.from_pretrained(model_version, output_attentions=True)

    """
    # Phrases avec le verbe 'courir'
    phrases = [
        "Il court un péril en allant là-bas.",
        "Le buzz court sur les réseaux sociaux.",
        "Le bruit court dans les couloirs.",
        "Elle court sur la route.",
        "Le danger court dans les zones inexplorées.",
        "Le nuage court dans le ciel orageux.",
        "Le risque court dans chaque décision d'investissement."
    ]
    """

    """
    # Phrases avec le verbe 'faire'
    phrases = [
        "Il fait marche arrière concernant ma décision.",
        "Elle fait la lessive tous les samedis pour garder mes vêtements propres.",
        "Julien fait du vélo tous les matins pour rester en forme.",
        "Il fait souvent du cinéma pour attirer la pitié.",
        "On fait une demande officielle pour obtenir l'autorisation nécessaire.",
        "Coralie fait de la boxe pour améliorer ma condition physique et ma concentration."
    ]
    """
    
    
    phrases = [
        "Je vis actuellement une tragédie avec le départ de mon père.",
        "Je vis dans le désert depuis mon arrivée ici.",
        "Je vis un conte de fées depuis que je l'ai rencontré",
        "C'est pour cette raison que je vis chez moi depuis tout ce temps"
    ]
    


    # Verbe à analyser
    word = 'vis' # faire / vivre / courir


    # Initialisation de la liste pour stocker tous les embeddings
    all_embeddings = []
    
    results = []  # Initialisation de la liste pour stocker les résultats
    # Comparer chaque paire de phrases
    for phrase1, phrase2 in itertools.combinations(phrases, 2):
        tokens1 = [token.lower() for token in tokenizer.tokenize(phrase1)]
        tokens2 = [token.lower() for token in tokenizer.tokenize(phrase2)]

        index_word1 = next((i for i, token in enumerate(tokens1) if word in token), None)
        index_word2 = next((i for i, token in enumerate(tokens2) if word in token), None)

        if index_word1 is not None and index_word2 is not None:
            inputs1 = tokenizer.encode_plus(phrase1, return_tensors='pt')
            inputs2 = tokenizer.encode_plus(phrase2, return_tensors='pt')

            with torch.no_grad():
                outputs1 = model(**inputs1)
                outputs2 = model(**inputs2)

            embedding1 = outputs1.last_hidden_state[0, index_word1, :]
            embedding2 = outputs2.last_hidden_state[0, index_word2, :]
            all_embeddings.append(embedding1)
            all_embeddings.append(embedding2)
            similarity = 1 - cosine(embedding1.numpy(), embedding2.numpy())
            results.append(f"Similarity for '{word}' between '{phrase1}' and '{phrase2}': {similarity:.2f}")
        else:
            results.append(f"Impossible de calculer la similarité entre '{phrase1}' et '{phrase2}' car le mot '{word}' n'est pas trouvé dans une des deux phrases.")
    return(results)

results = similarityCalcul(model_version)
for result in results:
    print(result)
    
# Extraction des attentions
attentions1 = outputs1.attentions
attentions2 = outputs2.attentions
# Analyse des attentions pour la première phrase
layer_attentions = attentions1[4]  # choix de la couche 
attention_scores = layer_attentions[0, :, index_word1, :]  # Attention scores du mot 
print(attention_scores)

Similarity for 'vis' between 'Je vis actuellement une tragédie avec le départ de mon père.' and 'Je vis dans le désert depuis mon arrivée ici.': 0.44
Similarity for 'vis' between 'Je vis actuellement une tragédie avec le départ de mon père.' and 'Je vis un conte de fées depuis que je l'ai rencontré': 0.43
Similarity for 'vis' between 'Je vis actuellement une tragédie avec le départ de mon père.' and 'C'est pour cette raison que je vis chez moi depuis tout ce temps': 0.44
Similarity for 'vis' between 'Je vis dans le désert depuis mon arrivée ici.' and 'Je vis un conte de fées depuis que je l'ai rencontré': 0.46
Similarity for 'vis' between 'Je vis dans le désert depuis mon arrivée ici.' and 'C'est pour cette raison que je vis chez moi depuis tout ce temps': 0.49
Similarity for 'vis' between 'Je vis un conte de fées depuis que je l'ai rencontré' and 'C'est pour cette raison que je vis chez moi depuis tout ce temps': 0.49
tensor([[7.3340e-01, 7.2851e-02, 2.1525e-02, 1.0932e-02, 2.5232e-02

In [9]:
model.eval()

CamembertModel(
  (embeddings): CamembertEmbeddings(
    (word_embeddings): Embedding(32005, 1024, padding_idx=1)
    (position_embeddings): Embedding(514, 1024, padding_idx=1)
    (token_type_embeddings): Embedding(1, 1024)
    (LayerNorm): LayerNorm((1024,), eps=1e-05, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): CamembertEncoder(
    (layer): ModuleList(
      (0-23): 24 x CamembertLayer(
        (attention): CamembertAttention(
          (self): CamembertSelfAttention(
            (query): Linear(in_features=1024, out_features=1024, bias=True)
            (key): Linear(in_features=1024, out_features=1024, bias=True)
            (value): Linear(in_features=1024, out_features=1024, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): CamembertSelfOutput(
            (dense): Linear(in_features=1024, out_features=1024, bias=True)
            (LayerNorm): LayerNorm((1024,), eps=1e-05, elementwise_affin

BERTviz for CamemBERT large

In [3]:
force_download=True
model_version = 'dangvantuan/sentence-camembert-large'
model = CamembertModel.from_pretrained(model_version, output_attentions=True)
tokenizer = CamembertTokenizer.from_pretrained(model_version)

#sentence_a = "Il porte son attention sur le problème."
#sentence_b = "Il porte un pot de miel à sa grand-mère."
#sentence_a = "Elle éprouve une immense haine pour lui."
#sentence_b = "Elle éprouve de grandes difficultés à finir son projet à temps "
sentence_a = "Le bruit court dans les couloirs."
sentence_b = "Elle court sur la route."
inputs = tokenizer(sentence_a, sentence_b, return_tensors='pt')
input_ids = inputs['input_ids']
attention_mask = inputs['attention_mask']

"""
# Boucle pour traiter chaque phrase
for sentence in phrases:
    inputs = tokenizer(sentence, return_tensors='pt', add_special_tokens=True)
    input_ids = inputs['input_ids']
    attention_mask = inputs['attention_mask']
"""

# Get model outputs, focusing on attentions
outputs = model(input_ids, attention_mask=attention_mask)
attention = outputs.attentions

# Convert input IDs back to tokens for visualization
tokens = tokenizer.convert_ids_to_tokens(input_ids[0])

head_view(attention, tokens)
model_view(attention, tokens, include_layers=[0,1,2,8,9])





<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>